# Augmentation Library Imgaug 설치

In [1]:
# !pip install imgaug

# 라이브러리 불러오기

In [2]:
import glob
import imageio
import imgaug as ia
from imgaug import augmenters as iaa
from imgaug.augmentables.bbs import BoundingBox, BoundingBoxesOnImage
import xml.etree.ElementTree as ET
from PIL import Image
import os
%matplotlib inline

# 변수 세팅

In [3]:
label_info_path = 'classes.txt' # 텍스트 파일 만들고 label 을 순서대로 적어 놓자 
# aug folder path
aug_folder = 'data'
# # img_file_path
# img_file_path = aug_folder + "/*.jpg"
# img_file_path2 = aug_folder + "/*.png"
#xml_file_path 
xml_file_path = aug_folder + "/*.xml"
#txt_file_path
txt_file_path = aug_folder + "/*.txt"

#save_dir
save_dir = "aug"
#save_label
save_label = save_dir +"\\"+ "label"
#save_img
save_img = save_dir +"\\"+"img"

#resize box size
box_size = 416
# Augmentation을 할 옵션들을 선택
augs = ["Add","Dropout","MotionBlur","AddtiveGaussianNoise","Sharpen","Emboss","Scale","Shear","CropAndPad","WithBrightnessChannels","HorizontalFlip"]
#['Identity']

#input format - xml, txt
input_format = 'xml'
#save format, yolo, xml 지금은 yolo만 구현
save_format = 'yolo'

#반복 횟수
iter_num = 10

## label mapping 중

In [4]:
labelmap ={}
labellist = []
with open(label_info_path, mode='r', encoding='utf-8') as f:
    label_list = f.readlines()
for i,label in enumerate(label_list):
    labelmap[label.replace('\n',"")] = i
    labellist.append(label.replace('\n',""))

# augmentation 할 파일 경로 리스트 세팅

In [5]:
## augmentation 할 파일 경로 리스트 세팅

# img_path_list = glob.glob(img_file_path)
# img_path_list.append(glob.glob(img_file_path2))
if input_format == 'xml':
    xml_path_list = glob.glob(xml_file_path)
elif input_format == 'txt':        
    txt_path_list = glob.glob(txt_file_path)

In [6]:
# xml_path_list

In [7]:
# txt_path_list

# Augmentation 기능 매핑 및 추가

링크 타고 가서 어떤 효과인지는 찾아보세요 
https://imgaug.readthedocs.io/en/latest/source/overview/geometric.html


In [8]:
# aug 종류
#너무 많아서 손아파서 못쓰겠다 알아서 써라 


# augmentation 리스트 초기화
aug_list = []

if "Identity" in augs: #아무것도 안함
    aug_list.append(iaa.Identity())
if "Add" in augs:
    aug_list.append(iaa.Add((-40,40)))
if "AddElementwise" in augs:
    aug_list.append(iaa.AddElementwise((-40, 40)))
if "AddtiveGaussianNoise" in augs:
    aug_list.append(iaa.AdditiveGaussianNoise(scale=(0, 0.2*255), per_channel=True))
    aug_list.append(iaa.AdditiveGaussianNoise(scale=(0, 0.2*255)))
if "AddtiveLaplaceNoise" in augs:
    aug_list.append(iaa.AddtiveLaplaceNoise(scale=(0,0.2*255)))
    aug_list.append(iaa.AddtiveLaplaceNoise(scale=(0,0.2*255), per_channel=True))
if "AddtivePoissonNoise" in augs:
    aug_list.append(iaa.AdditivePoissonNoise(scale=(0, 40)))
if "Multiply" in augs:
    aug_list.append(iaa.Multiply((0.5, 1.5)))
if "MultiplyElementwise" in augs:
    aug_list.append(iaa.Cutout(nb_iterations=(1,5), fill_mode="gaussian", fill_per_channel=True))
    aug_list.append(iaa.Cutout(fill_mode="gaussian", fill_per_channel=False))
if "Dropout" in augs:
    aug_list.append(iaa.Dropout(p=(0,0.2)))
    aug_list.append(iaa.Dropout(p=(0,0.2), per_channel=0.5))
if "CoarseDropout" in augs:
    aug_list.append(iaa.CoarseDropout((0.0, 0.05), size_percent=(0.02,0.25)))
    aug_list.append(iaa.CoarseDropout(0.02, size_percent=0.15, per_channel=0.5))
if "ImpulseNoise" in augs:
    aug_list.append(iaa.ImpulseNoise(0.1))
if "SaltAndPepper" in augs:
    aug_list.append(iaa.SaltAndPepper(0.1), per_channel=True)
if "CoarseSaltAndPepper" in augs:
    aug_list.append(iaa.CoarseSaltAndPepper(
    0.05, size_percent=(0.01, 0.1), per_channel=True))
if "Invert" in augs:
    aug_list.append(iaa.Invert(0.25, per_channel=0.5))
if "Solarize" in augs:
    aug_list.append(iaa.Solarize(0.5, threshold=(32,128)))
if "JpegComppression" in augs:
    aug_list.append(iaa.JpegCompression(compression=(70,99)))
if "Cartoon" in augs:
    aug_list.append(iaa.Cartoon())
if "GaussianBlur" in augs:
    aug_list.append(iaa.GaussianBlur(sigma=(0.0,3.0)))
if "AverageBlur" in augs:
    aug_list.append(iaa.AverageBlur(k=(2,11)))
if "MedianBlur" in augs:
    aug_list.append(iaa.MedianBlur(k=(3,11)))
if "BilateralBlur" in augs:
    aug_list.append(iaa.BilateralBlur(
    d=(3, 10), sigma_color=(10, 250), sigma_space=(10, 250)))
if "MotionBlur" in augs:
    aug_list.append(iaa.MotionBlur(k=10,angle=[-45, 45]))
if "MeanShiftBlur" in augs:
    aug_list.append(iaa.MeanShiftBlur())
if "RandAugment" in augs: # 아무거나 적용하는 듯?
    aug_list.append(iaa.RandAugment(n=2,m=9))
    aug_list.append(iaa.RandAugment(m=30))
    aug_list.append(iaa.RandAugment(m=(0,9)))
if "WithColorspace" in augs:
    aug_list.append(iaa.WithColorspace(
    to_colorspace="HSV",
    from_colorspace="RGB",
    children=iaa.WithChannels(
        0,
        iaa.Add((0, 50))
    )
))
if "WithBrightnessChannels" in augs:
    aug_list.append(iaa.WithBrightnessChannels(iaa.Add((-50, 50))))
if "ChangeColorTemperature" in augs:
    aug_list.append(iaa.ChangeColorTemperature((1100, 10000)))
if "KMeansColorQuantization" in augs:
    aug_list.append(iaa.KMeansColorQuantization(n_colors=(4, 16)))
if "UniformColorQuantization" in augs:
    aug_list.append(iaa.UniformColorQuantization(n_colors=(4, 16)))
if "HorizontalFlip" in augs:
    aug_list.append(iaa.HorizontalFlip())
if "VerticalFlip" in augs:
    aug_list.append(iaa.VerticalFlip())
if "Fliplr" in augs:
    aug_list.append(iaa.Fliplr(0.5))
if "Fog" in augs:
    aug_list.append(iaa.imgcorruplike.Fog(severity=2))
if "Frost" in augs:
    aug_list.append(iaa.imgcorruplike.Frost(severity=2))
if "Snow" in augs:
    aug_list.append(iaa.imgcorruplike.Snow(severity=2))
if "Spatter" in augs:
    aug_list.append(iaa.imgcorruplike.Spatter(severity=2))
if "Pixelate" in augs:
    aug_list.append(iaa.imgcorruptlike.Pixelate(severity=2))
if "FastSnowyLandscape" in augs:
    aug_list.append(iaa.FastSnowyLandscape(
    lightness_threshold=[128, 200],
    lightness_multiplier=(1.5, 3.5)
))
if "Clouds" in augs:
    aug_list.append(iaa.Clouds())
if "Snowflakes" in augs:
    aug_list.append(flake_size=(0.2, 0.7), speed=(0.007, 0.03))
if "Rain" in augs:
    aug_list.append(iaa.Rain(speed=(0.1, 0.3)))
if "GammaContrast" in augs:
    aug_list.append(iaa.GammaContrast((0.5, 2.0)))
if "SigmoidContrast" in augs:
    aug_list.append(iaa.SigmoidContrast(gain=(3, 10), cutoff=(0.4, 0.6)))
if "LogContrast" in augs:
    aug_list.append(iaa.LogContrast(gain=(0.6,1.4)))
if "LinearContrast" in augs:
    aug_list.append(iaa.LinearContrast((0.4,1.6)))
if "CKAGE" in augs:
    aug_list.append(iaa.AllChannelsCLAHE(clip_limit=(1, 10)))
if "AllChannelsHistogramEqualization" in augs:
    aug_list.append(iaa.Alpha((0.0, 1.0), iaa.AllChannelsHistogramEqualization()))
if "Convolve" in augs:
    matrix = np.array([[0, -1, 0],
                   [-1, 4, -1],
                   [0, -1, 0]])
    aug_list.append(iaa.Convolve(matrix=matrix))
if "Sharpen" in augs:
    aug_list.append(iaa.Sharpen(alpha=(0.0, 1.0), lightness=(0.75, 2.0)))
if "Emboss" in augs:
    aug_list.append(iaa.Emboss(alpha=(0.0,1.0), strength=(0.5,1.5)))
if "Scale" in augs:
    aug_list.append(iaa.Affine(scale=(0.5, 1.5)))
if "Rotate" in augs:
    aug_list.append(iaa.Affine(rotate=(-45,45)))
if "Shear" in augs:
    aug_list.append(iaa.Affine(shear=(-16,16)))
if "PiecewiseAffine" in augs:
    aug_list.append( iaa.PiecewiseAffine(scale=(0.01, 0.05)))
if "PerspectiveTransform" in augs:
    aug_list.append(iaa.PerspectiveTransform(scale=(0.01, 0.15)))
if "ElasticTransformation" in augs:
    aug_list.append(iaa.ElasticTransformation(alpha=(0, 5.0), sigma=0.25))
if "CropAndPad" in augs:
    aug_list.append(iaa.CropAndPad(
        percent=(-0.05, 0.1),
            pad_mode=ia.ALL,
            pad_cval=(0, 255)
    ))

In [9]:
aug_list

[Add(name=UnnamedAdd, parameters=[Uniform(Deterministic(int -40), Deterministic(int 40)), Deterministic(int 0)], deterministic=False),
 AdditiveGaussianNoise(name=UnnamedAdditiveGaussianNoise, parameters=[Normal(loc=Deterministic(int 0), scale=Uniform(Deterministic(int 0), Deterministic(float 51.00000000))), Deterministic(int 1)], deterministic=False),
 AdditiveGaussianNoise(name=UnnamedAdditiveGaussianNoise, parameters=[Normal(loc=Deterministic(int 0), scale=Uniform(Deterministic(int 0), Deterministic(float 51.00000000))), Deterministic(int 0)], deterministic=False),
 Dropout(name=UnnamedDropout, parameters=[Binomial(Uniform(Deterministic(float 0.80000000), Deterministic(int 1))), Deterministic(int 0)], deterministic=False),
 Dropout(name=UnnamedDropout, parameters=[Binomial(Uniform(Deterministic(float 0.80000000), Deterministic(int 1))), Binomial(Deterministic(float 0.50000000))], deterministic=False),
 MotionBlur(name=UnnamedMotionBlur, parameters=[<imgaug.augmenters.blur._MotionBlu

# Augmentation 객체 생성

In [10]:
seq = iaa.Sequential( ## 선택된 augmentator 중에서 0~전체 개수의 augmentator에서 랜덤한 순서대로 선택하여 진행
    iaa.SomeOf((0, None),
              aug_list,
              random_order=True)
)
seq2 = iaa.Sequential( ## 하나만 랜덤하게 골라서 진행
    iaa.OneOf(aug_list)
)

# VOC 형식의 XML 데이터에서 바운딩 박스와 라벨 데이터 추출하는 함수

In [11]:
def getXMLDATA(file_path):
    tree = ET.parse(file_path)
    root = tree.getroot() # 루트 파싱
    file_info ={}
    objects_list = []
    x = file_path.split('\\')
    x.reverse()
    #파일 명 추가
    file_info['filename'] = x[0]
    #사진 크기 추가
    file_info['width'] = root.find("size").find("width").text
    file_info['height'] = root.find("size").find("height").text
    #object 리스트 추가 
    for o in root.iter('object'):
        bndbox = {}
        bndbox['label'] = o.find("name").text # 라벨링 추가 
        sizes = []
        sizes.append(o.find("bndbox").find("xmin").text)
        sizes.append(o.find("bndbox").find("ymin").text)
        sizes.append(o.find("bndbox").find("xmax").text)
        sizes.append(o.find("bndbox").find("ymax").text)
        bndbox["bndbox"] = sizes
        objects_list.append(bndbox)
    file_info['objects'] = objects_list
    return file_info

# yolov Darknet 의 txt 데이터에서 바운딩 박스와 라벨 데이터 추출

In [12]:
def getImgSize(img_path):
    image = Image.open(img_path)
    width, height = image.size
    size =[]
    size.append(width)
    size.append(height)
    return size

def getYoloDATA(file_path, img_size):
    with open(file_path, mode='r', encoding='utf-8') as f:
        datas=f.readlines()
    file_info = {}
    x = file_path.split('\\')
    x.reverse()
    #파일 명 추가
    file_info['filename'] = x[0]
    #사진 크기 추가
    file_info['width'] = img_size[0]
    file_info['height'] = img_size[1]
    #object 리스트 추가
    objects_list = []
    for i in datas:
        i = i.replace("\n","")
        bndbox = {}
        temp = i.split(' ')
        bndbox['label'] = temp[0]
        sizes = []
        xmax = (float(temp[1])*img_size[0]*2 + float(temp[3])*img_size[0])/2.0
        xmin = (float(temp[1])*img_size[0]*2 - float(temp[3])*img_size[0])/2.0
        ymax = (float(temp[2])*img_size[1]*2 + float(temp[4])*img_size[1])/2.0
        ymin = (float(temp[2])*img_size[1]*2 - float(temp[4])*img_size[1])/2.0
        sizes.append(xmin)
        sizes.append(ymin)
        sizes.append(xmax)
        sizes.append(ymax)
        bndbox['bndbox'] = sizes
        objects_list.append(bndbox)
    file_info['objects'] = objects_list
    return file_info
        


# XML file Augmentation 진행 ->save yolo

In [13]:
if input_format == 'xml':
    for k in range(iter_num):
        for i, path in enumerate(xml_path_list):
            data = getXMLDATA(path)
            #확장자 버리고 이름만 따기
            name = data['filename'].split('.')
            name = name[0]
            #이미지 읽어오기
            img_path = ""
            if os.path.isfile(aug_folder+'\\'+name+'.jpg'):
                img_path +=  aug_folder+'\\'+name+'.jpg'
            else:
                img_path +=  aug_folder+'\\'+name+'.png'
            image = imageio.imread(img_path)
            #이미지 416 으로 리사이즈
            image = ia.imresize_single_image(image,(box_size,box_size))

            #resize 이후 라벨링 비율을 바꾸기 위함
            x_ratio = box_size/int(data["width"])
            y_ratio = box_size/int(data["height"])

            # 라벨 데이터와 바운딩 박스를 분리
            objects = data["objects"]

            text_list = []
            bbs_list = []

            for obj in objects:
                text_list.append(str(labelmap[obj['label']])) #라벨들을 미리 숫자로 바꾸고 text 앞부분에 저장        
                bbs = BoundingBox(x1=round(float(obj['bndbox'][0])*x_ratio),
                                  y1=round(float(obj['bndbox'][1])*y_ratio),
                                  x2=round(float(obj['bndbox'][2])*x_ratio),
                                  y2=round(float(obj['bndbox'][3])*y_ratio))
                bbs_list.append(bbs)
        #         ia.imshow(bbs.draw_on_image(image, size=2)) # 이미지 출력해서 원본 이미지 라벨링 보고 싶다면 ㄱ
            #바운딩 박스 객체 생성
            bounding_box = BoundingBoxesOnImage(bbs_list, shape=image.shape)
            # augmentation 진행
            img_aug, bbs_aug = seq(image=image, bounding_boxes=bounding_box)
            

        #     ia.imshow(bbs_aug.draw_on_image(img_aug, size=2)) # 변환된 이미지 보고 싶다면 ㄱ

            # numpy 형식의 데이터인 이미지를 저장
            try: # 폴더 경로가 없는 경우 생성
                if not(os.path.isdir(save_img)):
                    os.makedirs(os.path.join(save_img))
                if not(os.path.isdir(save_label)):
                    os.makedirs(os.path.join(save_label))
            except OSError as e:
                if e.errno != errno.EXIST:
                    print("Failed to create directory!!!!!")
                    raise


            if save_format == "yolo":
                im = Image.fromarray(img_aug)
                im.save(save_img+"\\"+name+'_aug' + str(k)+ '.jpg')


                for i,box in enumerate(bbs_aug):
                    dw = 1./box_size
                    dh = 1./box_size
                    
                    xmin = box[0][0]
                    ymin = box[0][1]
                    xmax = box[1][0]
                    ymax = box[1][1]
                    
                    if xmin <0: xmin = 0
                    elif xmin >box_size: xmin = box_size
                    
                    if ymin <0: ymin = 0
                    elif ymin >box_size: ymin = box_size
                        
                    if xmax <0: xmax = 0
                    elif xmax >box_size: xmax = box_size
                        
                    if ymax <0: ymax = 0
                    elif ymax >box_size: ymax = box_size
                        
                    print(xmin,ymin, xmax,ymax)
                    
                    x = ((xmin+xmax)/2.0)*dw
                    y = ((ymin+ymax)/2.0)*dh
                    w = (xmax - xmin)*dw                
                    h = (ymax - ymin)*dh      
                    
                    text_list[i] += ' ' + str(x) +' '+ str(y)  +' ' + str(w) +' ' +str(h)

                for i in text_list:
                    with open(save_label+"\\"+name+'_aug' + str(k)+ '.txt', mode='wt', encoding='utf-8') as f:
                        f.write(i+'\n')

    with open(save_img+'\\'+"classes.labels", mode='wt', encoding='utf-8') as f:
        for i in labellist:
            f.write(i+'\n')

184.0 203.0 208.0 216.0
134.0 196.0 181.0 213.0
84.0 197.0 134.0 211.0
194.0 210.0 206.0 218.0
173.41716 196.09842 189.61197 202.12215
154.47127 198.07996 157.00398 201.6892
160.93562 198.39941 162.90671 202.5618
156.88956 192.95654 175.55989 201.42514
138.00087 198.43114 141.59972 199.76974
164.99223 185.76578 185.37616 193.15715
157.51895 174.90904 184.71059 189.02383
116.22858 174.62263 139.76411 186.23445
137.98279 181.51895 159.54726 188.96843
166.98138 196.36113 177.77792 200.37695
241.6131 197.10954 248.16328 198.59337
309.26544 202.77809 317.7009 206.67775
283.94098 200.9471 288.8062 204.09033
269.5561 183.92009 301.4127 197.10286
253.93347 180.80725 282.63843 189.76958
245.27966 176.87856 264.51166 184.79404
220.51688 175.65878 241.49107 183.07921
311.37955 198.2078 316.15897 199.60448
309.8843 203.97148 315.87286 206.00844
242.20337 196.55641 245.24055 198.44815
286.08832 255.32191 288.50662 256.60245
240.53351 241.99529 247.14093 244.64343
218.97955 229.85934 256.53857 239.2

212.27502 200.33693 260.74423 345.51648
244.34338 200.72714 307.6694 353.55325
0 147.70448 416 378.0427
14.212583 0 416 243.70226
1.6939095 127.87668 409.01166 250.47911
0 0 402.51324 228.77908
0 129.81154 416 314.28265
202.72935 121.98694 292.62906 320.88214
296.70883 92.16775 369.23572 292.166
234.40489 325.82208 244.13557 339.1021
207.345 340.52496 222.16765 358.6934
181.61813 354.7458 186.8167 365.447
0.0 1.0 311.0 300.0
328.0 176.0 393.0 416.0
343.0 228.0 416.0 416.0
0 215.45662 143.87305 297.47946
234.84384 273.6183 352.65848 340.72787
0 0 386.95892 319.84933
216.11499 136.33614 381.83163 319.86554
236.61601 282.2857 383.54004 390.65546
124.7146 153.81512 195.61397 387.15967
64.065704 147.69748 123.86038 265.6807
31.605743 33.210087 187.92609 282.2857
117.09629 256.8163 224.94815 307.7551
149.96544 78.53061 163.31851 97.63266
178.72592 87.02041 196.18765 100.81633
169.48148 151.7551 200.2963 188.89795
213.64938 98.69388 228.02963 123.10204
230.08394 176.16327 270.14322 215.42857


99.921265 229.32886 171.08707 300.4404
223.333 215.3289 306.54196 286.7172
74.606415 96.83422 293.08395 251.98438
294.90448 94.208565 382.01022 203.89578
84.825775 10.650001 405.85257 216.50941
93.85914 90.43054 353.94937 270.54147
112.57186 177.59698 165.12204 359.20645
288.45486 152.13148 332.10822 356.84772
323.43958 231.14389 352.36856 269.27298
158.473 90.4784 298.93356 260.33255
108.68825 135.35394 114.708664 154.24255
109.4102 229.90987 115.24184 239.73645
345.0 233.0 378.0 291.0
15.0 341.0 55.0 398.0
233.0 256.0 318.0 307.0
0.0 27.0 197.0 329.0
291.0 156.0 355.0 343.0
188.0 157.0 240.0 382.0
196.0 48.0 416.0 359.0
41.0 253.0 108.0 387.0
181.0 262.0 244.0 378.0
296.0 269.0 336.0 375.0
0.0 286.0 60.0 323.0
116.0 310.0 165.0 339.0
0.0 256.0 416.0 314.0
207.0 17.0 363.0 174.0
1.0 1.0 226.0 270.0
163.02193 17.199057 416 183.4069
0 7.4740787 408.5195 416
138.45813 144.15425 234.79358 401.47226
65.0 1.0 330.0 416.0
180.0 83.0 214.0 254.0
0 129.17073 416 345.5929
0 0 416 235.23193
150.

96.0 48.0 349.0 171.0
0 86.1338 416 416
110.67478 60.779182 222.59363 197.3882
248.66798 62.214703 349.30316 205.86295
45.0 44.0 211.0 153.0
234.0 253.0 285.0 401.0
372.0 202.0 416.0 304.0
43.0 230.0 159.0 294.0
0.0 1.0 351.0 230.0
31.057213 0 261.87314 343.32773
171.00325 7.0650625 416 394.55942
0 44.439713 155.64691 384.76715
114.79248 0 394.41504 295.91165
157.30698 234.44075 218.04437 360.7138
226.54785 294.08115 263.05972 370.65805
329.73715 314.40103 356.25482 390.9281
74.0 115.0 416.0 386.0
186.0 174.0 245.0 377.0
0 205.27481 0 322.45807
113.67165 0 416 276.1298
300.86594 280.2176 416 387.86264
40.54545 0 416 416
23.0 131.0 416.0 345.0
219.0 358.0 256.0 416.0
109.929474 120.99168 305.67783 305.8815
217.19545 258.1747 249.91396 301.0681
64.24945 95.71438 396.06213 219.97961
59.591904 0 415.54678 145.00879
157.0 14.0 392.0 308.0
1.0 2.0 414.0 331.0
161.0 152.0 339.0 293.0
1.0 1.0 154.0 208.0
88.34186 99.93553 416 360.032
135.79312 0.66533965 416 157.93884
11.953964 57.771084 397.4

33.5632 160.38705 382.463 227.86385
119.0 91.0 377.0 238.0
0 176.2729 416 416
30.550262 186.01723 218.48547 330.58655
64.13705 11.160975 405.3105 308.4488
168.15205 220.6506 416 397.6121
1.0 1.0 416.0 283.0
4.518193 7.7770205 408.554 416
35.349834 0 401.25818 368.01224
86.72677 155.65184 389.4736 313.5688
171.23355 191.05644 254.54666 290.28064
318.65622 281.4637 377.42596 350.57425
43.41989 265.1072 100.99881 332.12558
0 0 368.68036 326.87848
28.81079 23.69634 379.89734 356.7443
78.75592 234.38614 306.53683 382.24164
0.0 82.0 402.0 382.0
0 0 416 416
0 149.89551 416 416
82.87695 165.3 416 353.12762
20.0 146.0 381.0 338.0
25.250423 160.61691 410.71893 332.888
27.0 1.0 352.0 331.0
0 0 416 369.33676
308.69623 20.656855 415.3877 416
0.0 7.0 415.0 248.0
145.39075 103.439095 299.2079 203.70673
113.31961 0 385.40082 388.19092
0 0 416 282.83163
12.0 187.0 322.0 416.0
87.05106 22.265146 336.42957 387.01523
225.0 6.0 342.0 296.0
237.1144 322.21213 416 367.0936
189.0505 261.97025 416 376.5464
78.

...

0 334.00546 23.823166 366.93982
120.039314 300.0301 141.51567 332.44595
272.43277 391.3972 286.55292 414.17838
380.9281 392.88623 390.24545 410.0631
247.60017 42.57095 259.1668 61.32175
132.3175 148.97545 142.24321 171.06529
0 348.45386 0 351.256
0 345.63327 0 350.8919
0 343.84976 0 349.1084
0 344.5411 0.43355152 347.34323
4.6120467 349.43564 9.414826 355.03992
8.958584 348.89874 13.761361 354.50302
13.153035 349.5901 16.907202 355.0215
16.603035 350.10855 20.053043 353.08353
20.949574 348.34344 24.551659 352.54663
23.503044 343.77615 26.2086 349.03473
26.056519 340.43707 28.762068 345.69568
28.457903 337.09805 32.36415 343.75775
34.91762 328.13635 37.775257 334.6232
37.775257 324.7973 41.377342 329.0005
40.328728 321.45822 46.028038 326.0071
46.62041 323.72348 49.0218 326.5256
51.119026 321.9583 52.471798 324.5876
53.21626 319.84753 62.21349 326.14313
62.21349 317.5455 65.81557 321.7487
66.25586 320.6933 70.75448 323.84106
70.75448 317.6999 74.35656 321.9031
75.25309 315.93475 82.0010

36.060307 0 416 356.7009
299.77365 72.610275 333.26376 99.3241
292.2984 276.74402 309.37292 285.84473
247.40836 130.29938 255.33244 144.78607
132.16888 88.04682 241.57625 156.15741
39.585297 86.31419 120.49281 108.911415
47.531338 299.81558 273.38092 335.75513
150.36658 339.96112 173.64696 367.03842
171.15842 324.8708 190.19473 354.0397
208.52534 194.23013 324.86743 344.85223
0 0 416 416
0 63.21627 416 359.66864
52.878822 11.351229 360.3737 306.84332
1.0 1.0 416.0 288.0
143.1035 103.5572 313.45682 269.85446
146.65253 269.85446 213.57704 290.64163
234.3642 240.44824 259.2074 264.27744
27.130434 24.625793 403.33914 352.6765
0.3076172 15.278161 367.08353 400.72183
0 0 416 252.4743
1.0 75.0 416.0 412.0
89.97813 100.06673 340.1922 315.6179
168.0 375.0 185.0 415.0
208.0 312.0 260.0 396.0
1.0 1.0 134.0 416.0
137.0 1.0 416.0 350.0
1.0 0.0 416.0 328.0
52.0 349.0 71.0 362.0
123.0 144.0 139.0 154.0
107.0 214.0 115.0 221.0
31.0 214.0 53.0 223.0
65.0 334.0 78.0 344.0
83.0 152.0 339.0 372.0
0.0 1.0 

160.07513 258.57916 171.5771 267.8692
204.16602 211.61281 239.63043 248.2569
212.7925 203.35498 236.27567 212.12892
182.59982 169.80757 216.14722 188.38766
184.51682 194.06493 186.4338 197.1616
177.32808 198.70995 179.24509 201.29053
198.89427 198.70995 201.29053 201.29053
203.68675 202.83887 207.0415 205.93555
206.08301 217.80617 210.8755 222.45119
172.5356 157.42084 174.93184 161.03363
156.24115 152.2597 157.6789 156.38861
153.8449 151.74359 155.28265 154.84027
166.30536 166.19478 167.74312 169.29146
165.82611 123.87343 167.74312 126.97011
191.22629 160.0014 208.9585 170.8398
200.81126 147.09856 217.58498 156.38861
221.89821 131.61514 226.21146 134.19571
212.7925 133.16348 215.66797 146.06633
204.16602 129.55067 208.9585 136.77628
206.56226 123.87343 209.91699 126.97011
211.83398 127.48622 215.18874 130.5829
2.0 19.0 416.0 288.0
0 0 416 202.51393
1.4588077 115.44305 79.36741 164.03072
154.01012 127.08181 195.31577 163.17337
175.81294 98.64293 274.25595 164.21457
318.49603 298.99573 3

98.83094 20.299206 341.47635 355.07043
67.210075 0 416 362.26596
0 211.29292 416 365.12592
0 0 416 339.50967
28.951933 0 324.3155 293.60367
0 0 416 348.21753
187.90913 178.5673 236.83022 241.09953
207.53227 67.8634 302.73254 211.24115
104.32589 73.607635 344.69623 242.55804
85.63983 105.44517 308.07574 274.8343
71.0 1.0 342.0 317.0
265.0 342.0 287.0 415.0
342.0 333.0 409.0 416.0
121.0 3.0 307.0 359.0
273.0 287.0 305.0 382.0
180.16545 307.11407 254.05353 363.88367
1.0121654 22.335571 416 350.85458
105.30516 91.82636 271.36267 209.30006
258.3932 197.53479 271.1908 205.46907
233.60663 202.63123 244.05249 207.76933
223.8375 198.05428 228.60187 206.95535
210.5458 200.03647 221.65826 210.14738
196.15436 199.24193 203.26035 210.3877
0 14.045106 416 327.27676
79.48387 14.716981 327.2258 301.20755
122.838715 293.3585 170.32259 302.1887
28.903225 279.62265 37.16129 301.20755
54.709675 281.5849 61.935482 302.1887
61.935482 281.5849 68.129036 301.20755
56.555504 50.135258 372.1391 391.89563
184.17

0 0 416 416
93.338196 382.40402 116.52356 415.85922
0.0 0.0 416.0 398.0
88.0 208.0 290.0 316.0
251.01918 333.52505 346.81448 394.24835
113.53519 292.74075 180.0597 351.65143
49.671642 232.92375 80.716415 275.5207
84.26439 137.76035 110.8742 281.86493
109.987206 164.94989 122.40511 232.92375
125.953094 196.67102 134.82303 243.79956
104.66524 227.48584 135.71002 277.33334
210.21748 241.08061 235.05331 264.64487
304.2388 309.9608 317.5437 333.52505
333.5096 319.93027 341.49252 336.24402
200.46056 23.56427 351.24948 324.46185
109.4563 277.00974 149.53278 339.1437
0 0 416 388.2683
219.69922 351.87308 227.69952 362.32278
124.39235 91.81564 276.81528 381.67807
0 0 340.30142 407.1817
211.0 293.0 260.0 361.0
166.0 351.0 184.0 382.0
1.0 1.0 416.0 415.0
147.3298 83.88657 305.18155 268.36398
90.56158 119.09474 194.53096 292.3815
0 23.681124 416 294.8279
39.003235 134.85777 381.12308 290.7348
96.02888 254.93756 166.05556 294.51956
92.72477 27.214315 327.93976 321.96735
48.0 234.0 56.0 254.0
147.0 1

# Yolo augmentation ->yolo save

In [14]:
if input_format == 'txt':
    for k in range(iter_num):
        for i, path in enumerate(txt_path_list):
            
            #확장자 버리고 이름만 따기
            temp = path.split('\\')
            temp.reverse()
            txt_file_name = temp[0].split('.txt')
            name = txt_file_name[0]
            #이미지 읽어오기
            img_path = ""
            if os.path.isfile(aug_folder+'\\'+name+'.jpg'):
                img_path +=  aug_folder+'\\'+name+'.jpg'
            else:
                img_path +=  aug_folder+'\\'+name+'.png'
            image = imageio.imread(img_path)
            
            #이미지 416 으로 리사이즈
            image = ia.imresize_single_image(image,(box_size,box_size))
            
            #txt 데이터 
            data = getYoloDATA(path,getImgSize(img_path))

            #resize 이후 라벨링 비율을 바꾸기 위함
            x_ratio = box_size/int(data["width"])
            y_ratio = box_size/int(data["height"])

            # 라벨 데이터와 바운딩 박스를 분리
            objects = data["objects"]

            text_list = []
            bbs_list = []

            for obj in objects:
                text_list.append(str(obj['label'])) #라벨들을 미리 숫자로 바꾸고 text 앞부분에 저장        
                bbs = BoundingBox(x1=round(float(obj['bndbox'][0])*x_ratio),
                                  y1=round(float(obj['bndbox'][1])*y_ratio),
                                  x2=round(float(obj['bndbox'][2])*x_ratio),
                                  y2=round(float(obj['bndbox'][3])*y_ratio))
                bbs_list.append(bbs)
        #         ia.imshow(bbs.draw_on_image(image, size=2)) # 이미지 출력해서 원본 이미지 라벨링 보고 싶다면 ㄱ
            #바운딩 박스 객체 생성
            bounding_box = BoundingBoxesOnImage(bbs_list, shape=image.shape)
            # augmentation 진행
            img_aug, bbs_aug = seq(image=image, bounding_boxes=bounding_box)


        #     ia.imshow(bbs_aug.draw_on_image(img_aug, size=2)) # 변환된 이미지 보고 싶다면 ㄱ

            # numpy 형식의 데이터인 이미지를 저장
            try: # 폴더 경로가 없는 경우 생성
                if not(os.path.isdir(save_img)):
                    os.makedirs(os.path.join(save_img))
                if not(os.path.isdir(save_label)):
                    os.makedirs(os.path.join(save_label))
            except OSError as e:
                if e.errno != errno.EXIST:
                    print("Failed to create directory!!!!!")
                    raise


            if save_format == "yolo":
                im = Image.fromarray(img_aug)
                im.save(save_img+"\\"+name+'_aug' + str(k)+ '.jpg')

                for i,box in enumerate(bbs_aug):
                    dw = 1./box_size
                    dh = 1./box_size
                    
                    xmin = box[0][0]
                    ymin = box[0][1]
                    xmax = box[1][0]
                    ymax = box[1][1]
                    
                    if xmin <0: xmin = 0
                    elif xmin >box_size: xmin = box_size
                    
                    if ymin <0: ymin = 0
                    elif ymin >box_size: ymin = box_size
                        
                    if xmax <0: xmax = 0
                    elif xmax >box_size: xmax = box_size
                        
                    if ymax <0: ymax = 0
                    elif ymax >box_size: ymax = box_size
                        
                    print(xmin,ymin, xmax,ymax)
                    
                    x = ((xmin+xmax)/2.0)*dw
                    y = ((ymin+ymax)/2.0)*dh
                    w = (xmax - xmin)*dw                
                    h = (ymax - ymin)*dh      
                    
                  
                    text_list[i] += ' ' + str(x) +' '+ str(y)  +' ' + str(w) +' ' +str(h)

                for i in text_list:
                    with open(save_label+"\\"+name+'_aug' + str(k)+ '.txt', mode='wt', encoding='utf-8') as f:
                        f.write(i+'\n')

        with open(save_img+'\\'+"classes.labels", mode='wt', encoding='utf-8') as f:
            for i in labellist:
                f.write(i+'\n')

In [15]:
# if input_format == 'xml':
#     for k in range(1):
#         for i, path in enumerate(xml_path_list):
#             data = getXMLDATA(path)
#             #확장자 버리고 이름만 따기
#             name = data['filename'].split('.')
#             name = name[0]
#             #이미지 읽어오기
#             img_path = ""
#             if os.path.isfile(aug_folder+'\\'+name+'.jpg'):
#                 img_path +=  aug_folder+'\\'+name+'.jpg'
#             else:
#                 img_path +=  aug_folder+'\\'+name+'.png'
#             image = imageio.imread(img_path)
#             #이미지 416 으로 리사이즈
#             image = ia.imresize_single_image(image,(box_size,box_size))

#             #resize 이후 라벨링 비율을 바꾸기 위함
#             x_ratio = box_size/int(data["width"])
#             y_ratio = box_size/int(data["height"])

#             # 라벨 데이터와 바운딩 박스를 분리
#             objects = data["objects"]

#             text_list = []
#             bbs_list = []

#             for obj in objects:
#                 text_list.append(str(labelmap[obj['label']])) #라벨들을 미리 숫자로 바꾸고 text 앞부분에 저장        
#                 bbs = BoundingBox(x1=round(float(obj['bndbox'][0])*x_ratio),
#                                   y1=round(float(obj['bndbox'][1])*y_ratio),
#                                   x2=round(float(obj['bndbox'][2])*x_ratio),
#                                   y2=round(float(obj['bndbox'][3])*y_ratio))
#                 bbs_list.append(bbs)
#         #         ia.imshow(bbs.draw_on_image(image, size=2)) # 이미지 출력해서 원본 이미지 라벨링 보고 싶다면 ㄱ
#             #바운딩 박스 객체 생성
#             bounding_box = BoundingBoxesOnImage(bbs_list, shape=image.shape)
#             # augmentation 진행
#             img_aug, bbs_aug = seq(image=image, bounding_boxes=bounding_box)
            

#         #     ia.imshow(bbs_aug.draw_on_image(img_aug, size=2)) # 변환된 이미지 보고 싶다면 ㄱ

#             # numpy 형식의 데이터인 이미지를 저장
#             try: # 폴더 경로가 없는 경우 생성
#                 if not(os.path.isdir(save_img)):
#                     os.makedirs(os.path.join(save_img))
#                 if not(os.path.isdir(save_label)):
#                     os.makedirs(os.path.join(save_label))
#             except OSError as e:
#                 if e.errno != errno.EXIST:
#                     print("Failed to create directory!!!!!")
#                     raise


#             if save_format == "yolo":
#                 im = Image.fromarray(img_aug)
#                 im.save(save_img+"\\"+name+'_aug' + str(k)+ '.jpg')


#                 for i,box in enumerate(bbs_aug):
#                     dw = 1./box_size
#                     dh = 1./box_size
#                     if(box[1][0] > box_size): box[1][0] = box_size
#                     if(box[1][1] > box_size): box[1][1] = box_size
#                     x = ((int(box[0][0])+int(box[1][0]))/2.0)*dw
#                     y = ((int(box[0][1])+int(box[1][1]))/2.0)*dh
#                     w = (int(box[1][0]) - int(box[0][0]))*dw                
#                     h = (int(box[1][1]) - int(box[0][1]))*dh        
#                     text_list[i] += ' ' + str(x) +' '+ str(y)  +' ' + str(w) +' ' +str(h)

#                 for i in text_list:
#                     with open(save_label+"\\"+name+'_org_resize' + str(k)+ '.txt', mode='wt', encoding='utf-8') as f:
#                         f.write(i+'\n')

#     with open(save_img+'\\'+"classes.labels", mode='wt', encoding='utf-8') as f:
#         for i in labellist:
#             f.write(i+'\n')